# Creating a Betting Algorithm for Points

### Importing Packages

In [7]:
import pandas as pd
import numpy as np

In [9]:
import nba_api.stats.endpoints as me
from nba_api.stats.endpoints import playercareerstats
from nba_api.stats.static import players

from datetime import datetime

from sklearn.metrics import mean_squared_error, root_mean_squared_error
from sklearn.model_selection import cross_val_score,train_test_split, TimeSeriesSplit
from sklearn.metrics import mean_squared_error,r2_score
from sklearn.model_selection import KFold
from sklearn.tree import DecisionTreeRegressor
from sklearn.model_selection import GridSearchCV, ParameterGrid
from sklearn.linear_model import LassoCV, Lasso, LinearRegression
from sklearn.ensemble import BaggingRegressor, RandomForestRegressor, StackingRegressor, RandomForestClassifier, GradientBoostingClassifier, GradientBoostingRegressor
from sklearn.pipeline import Pipeline
from sklearn.preprocessing import PolynomialFeatures, StandardScaler

### Prelimary Data Gathering
##### Should not have to run any code under here up until making the actual model

In [11]:
player_details = me.PlayerIndex(league_id = '00', season = '2024-25').get_data_frames()[0]

def height_to_inches(height_str):
    # Split the height string into feet and inches
    feet, inches = height_str.split('-')
    
    # Convert to integers and calculate total height in inches
    total_inches = (int(feet) * 12) + int(inches)
    
    return total_inches

player_details['HEIGHT_INCHES'] = player_details['HEIGHT'].apply(height_to_inches)
player_details['WEIGHT'] = pd.to_numeric(player_details['WEIGHT'])
player_details['POSITION'] = player_details['POSITION'].apply(lambda x: x[0] if x is not None else 'G')
player_details['PLAYER'] = player_details['PLAYER_FIRST_NAME']+ ' '+ player_details['PLAYER_LAST_NAME']
player_details

PERSON_ID PLAYER_LAST_NAME PLAYER_FIRST_NAME       PLAYER_SLUG  \
0      1630173          Achiuwa          Precious  precious-achiuwa   
1       203500            Adams            Steven      steven-adams   
2      1628389          Adebayo               Bam       bam-adebayo   
3      1630534           Agbaji             Ochai      ochai-agbaji   
4      1630583           Aldama             Santi      santi-aldama   
..         ...              ...               ...               ...   
527     203469           Zeller              Cody       cody-zeller   
528    1627826            Zubac             Ivica       ivica-zubac   
529    1641783         da Silva           Tristan  tristan-da-silva   
530    1628427           Čančar            Vlatko     vlatko-čančar   
531     203967            Šarić             Dario       dario-šarić   

        TEAM_ID  TEAM_SLUG  IS_DEFUNCT TEAM_CITY  TEAM_NAME TEAM_ABBREVIATION  \
0    1610612752     knicks           0  New York     Knicks               NYK   
1    1610612745    rockets           0   Houston    Rockets               HOU   
2    1610612748       heat           0     Miami       Heat               MIA   
3    1610612761    raptors           0   Toronto    Raptors               TOR   
4    1610612763  grizzlies           0   Memphis  Grizzlies               MEM   
..          ...        ...         ...       ...        ...               ...   
527  1610612737      hawks           0   Atlanta      Hawks               ATL   
528  1610612746   clippers           0        LA   Clippers               LAC   
529  1610612753      magic           0   Orlando      Magic               ORL   
530  1610612743    nuggets           0    Denver    Nuggets               DEN   
531  1610612743    nuggets           0    Denver    Nuggets               DEN   

     ... DRAFT_NUMBER ROSTER_STATUS FROM_YEAR  TO_YEAR   PTS   REB  AST  \
0    ...         20.0           1.0      2020     2024   NaN   NaN  NaN   
1    ...         12.0           1.0      2013     2024   2.5   2.6  1.4   
2    ...         14.0           1.0      2017     2024  16.3   9.5  3.9   
3    ...         14.0           1.0      2022     2024  12.4   4.6  2.1   
4    ...         30.0           1.0      2021     2024  12.7   7.2  3.5   
..   ...          ...           ...       ...      ...   ...   ...  ...   
527  ...          4.0           1.0      2013     2024   NaN   NaN  NaN   
528  ...         32.0           1.0      2016     2024  15.1  12.5  2.5   
529  ...         18.0           1.0      2024     2024   7.4   4.0  1.9   
530  ...         49.0           1.0      2019     2024   2.3   2.0  0.0   
531  ...         12.0           1.0      2016     2024   3.4   3.5  1.1   

     STATS_TIMEFRAME  HEIGHT_INCHES            PLAYER  
0             Season             80  Precious Achiuwa  
1             Season             83      Steven Adams  
2             Season             81       Bam Adebayo  
3             Season             77      Ochai Agbaji  
4             Season             84      Santi Aldama  
..               ...            ...               ...  
527           Season             83       Cody Zeller  
528           Season             84       Ivica Zubac  
529           Season             80  Tristan da Silva  
530           Season             80     Vlatko Čančar  
531           Season             82       Dario Šarić  

[532 rows x 28 columns]

In [12]:
player_details.loc[player_details['PERSON_ID'] == 1628386, 'POSITION'].mode()[0]

'C'

In [13]:
id_list = [x for x in player_details['PERSON_ID']]


In [14]:
data = players.get_players()

In [15]:
df = pd.DataFrame(data)
active_df_24 = df.loc[df['is_active'] == True, :]
active_df_24.loc[active_df_24['first_name'] == 'Miles', :]

id      full_name first_name last_name  is_active
508   1628970  Miles Bridges      Miles   Bridges       True
2868  1630540  Miles McBride      Miles   McBride       True

### Pulling Player gamelogs for every player from 2022-23 and 2023-24

In [42]:
game_log_dict_23 = {}
game_log_dict_24 = {}

# Assuming 'df' is a DataFrame that contains the player IDs
#for 2023 season
for id in active_df_24.loc[:, 'id']:
    
    try:
        # Pull every game log for the 2023-24 season
        game_logs = me.PlayerGameLog(season='2022-23', player_id=id, season_type_all_star = 'Regular Season')

        # Get the game log data as a DataFrame
        game_log_df = game_logs.get_data_frames()[0]
        game_log_df['OPP'] = game_log_df['MATCHUP'].apply(lambda x: x[-3:])
        print(game_log_df['Player_ID'].unique()[0])
        # Store the DataFrame in the dictionary with the player ID as the key
        game_log_dict_23[game_log_df['Player_ID'].unique()[0]] = game_log_df
        
    except Exception as e:
        print(f"Error processing player {id}: {e}")

# for 2024 season
for id in active_df_24.loc[:, 'id']:
    
    try:
        # Pull every game log for the 2023-24 season
        game_logs = me.PlayerGameLog(season='2023-24', player_id=id, season_type_all_star = 'Regular Season')

        # Get the game log data as a DataFrame
        game_log_df = game_logs.get_data_frames()[0]
        game_log_df['OPP'] = game_log_df['MATCHUP'].apply(lambda x: x[-3:])
        print(game_log_df['Player_ID'].unique()[0])
        # Store the DataFrame in the dictionary with the player ID as the key
        game_log_dict_24[game_log_df['Player_ID'].unique()[0]] = game_log_df
        
    except Exception as e:
        print(f"Error processing player {id}: {e}")

1630173
1628389
1630534
1630583
1629638
1628960
1628386
Error processing player 1641851: index 0 is out of bounds for axis 0 with size 0
1630631
203937
203507
203648
1630175
1628384
1627853
1630166
Error processing player 1629028: HTTPSConnectionPool(host='stats.nba.com', port=443): Max retries exceeded with url: /stats/playergamelog?DateFrom=&DateTo=&LeagueID=&PlayerID=1629028&Season=2022-23&SeasonType=Regular+Season (Caused by ConnectTimeoutError(<urllib3.connection.HTTPSConnection object at 0x0000021B95E7C110>, 'Connection to stats.nba.com timed out. (connect timeout=30)'))
1628962
Error processing player 1630641: index 0 is out of bounds for axis 0 with size 0
1628963
Error processing player 1641735: index 0 is out of bounds for axis 0 with size 0
1631116
1630163
1628964
1631094
1630217
1630625
1631230
203084
1630567
1629628
1629646
Error processing player 1641734: index 0 is out of bounds for axis 0 with size 0
1628966
201587
1629647
203078
1627736
1630699
Error processing player 

In [118]:
# Example function to convert DataFrame to JSON-serializable format
def convert_dataframe_to_serializable(df):
    return df.applymap(lambda x: x.strftime('%Y-%m-%d %H:%M:%S') if isinstance(x, pd.Timestamp) else x).to_dict(orient='records')

# Convert DataFrames to JSON-serializable dictionaries
game_log_24_converted = {int(key): convert_dataframe_to_serializable(value) for key, value in game_log_dict_24.items()}
game_log_23_converted = {int(key): convert_dataframe_to_serializable(value) for key, value in game_log_dict_23.items()}

# Save the converted dictionary to a JSON file
with open('gamelogs_2023_24.json', 'w') as f:
    json.dump(game_log_24_converted, f)
with open('gamelogs_2022_23.json', 'w') as f:
    json.dump(game_log_23_converted, f)

C:\Users\jam2m\AppData\Local\Temp\ipykernel_24696\1972928286.py:3: FutureWarning: DataFrame.applymap has been deprecated. Use DataFrame.map instead.
  return df.applymap(lambda x: x.strftime('%Y-%m-%d %H:%M:%S') if isinstance(x, pd.Timestamp) else x).to_dict(orient='records')
C:\Users\jam2m\AppData\Local\Temp\ipykernel_24696\1972928286.py:3: FutureWarning: DataFrame.applymap has been deprecated. Use DataFrame.map instead.
  return df.applymap(lambda x: x.strftime('%Y-%m-%d %H:%M:%S') if isinstance(x, pd.Timestamp) else x).to_dict(orient='records')
C:\Users\jam2m\AppData\Local\Temp\ipykernel_24696\1972928286.py:3: FutureWarning: DataFrame.applymap has been deprecated. Use DataFrame.map instead.
  return df.applymap(lambda x: x.strftime('%Y-%m-%d %H:%M:%S') if isinstance(x, pd.Timestamp) else x).to_dict(orient='records')
C:\Users\jam2m\AppData\Local\Temp\ipykernel_24696\1972928286.py:3: FutureWarning: DataFrame.applymap has been deprecated. Use DataFrame.map instead.
  return df.applymap

In [22]:
# Load the JSON file
with open('gamelogs_2023_24.json', 'r') as f:
    game_log_24_converted = json.load(f)
with open('gamelogs_2022_23.json', 'r') as f:
    game_log_23_converted = json.load(f)

# Convert each entry back to a DataFrame
game_log_dict_24 = {int(key): pd.DataFrame(value) for key, value in game_log_24_converted.items()}
game_log_dict_23 = {int(key): pd.DataFrame(value) for key, value in game_log_23_converted.items()}

### Making sure each dictionary has the same y

In [25]:
id_list

[1630173,
 203500,
 1628389,
 1630534,
 1630583,
 1641725,
 1629638,
 1628960,
 1628386,
 1630631,
 203937,
 203507,
 1630175,
 1628384,
 1630166,
 1629028,
 1628963,
 1631116,
 1630163,
 1628366,
 1628964,
 1631094,
 1630217,
 1630625,
 1631230,
 203084,
 1630567,
 1629628,
 1629646,
 1641734,
 1642419,
 201587,
 203078,
 1627736,
 1630699,
 1641736,
 1630180,
 1629048,
 1641710,
 203992,
 202711,
 1629626,
 1641737,
 1626164,
 1630527,
 1628449,
 1631103,
 1631128,
 1641779,
 1628969,
 1628970,
 1627763,
 1628415,
 1628971,
 1627759,
 1641738,
 1629650,
 1628973,
 1628418,
 1641723,
 1642486,
 202692,
 1630215,
 202710,
 1641824,
 1631288,
 203484,
 1641739,
 203991,
 1642382,
 1642267,
 1642269,
 1628975,
 1628976,
 1630618,
 1627936,
 1642264,
 1630658,
 1630577,
 1630551,
 1642279,
 1642353,
 1631108,
 1630528,
 1631321,
 1641740,
 1629634,
 203903,
 1629651,
 1642270,
 1641730,
 1629599,
 1642268,
 1628381,
 1628380,
 201144,
 1626192,
 1641731,
 1641741,
 1628470,
 1642384,
 163

In [27]:
for k, v in game_log_dict_23.items():
    print(k)

1630173
1628389
1630534
1630583
1629638
1628960
1628386
1630631
203937
203507
1630175
1628384
1630166
1629028
1628963
1631116
1630163
1628964
1631094
1630217
1630625
1631230
203084
1630567
1629628
1629646
1641734
201587
203078
1627736
1630699
1630180
1629048
1641710
203992
202711
1629626
1626164
1630527
1628449
1631103
1631128
1628969
1628970
1627763
1628415
1628971
1627759
1641738
1628973
1628418
1641723
202692
1630215
202710
1631288
203484
1641739
203991
1628975
1628976
1630618
1627936
1630658
1630577
1630551
1631108
1631321
1629634
203903
1629651
1641730
1629599
1628381
1628380
201144
1626192
1641731
1641741
1628470
1630595
203552
201939
1630700
203076
1631098
1631120
201942
1628978
1631217
1641711
1631172
203915
1629029
1629652
1630245
1630288
203083
1630537
1630561
1627739
201142
1631105
1631106
1630162
1630556
1631165
203954
1629234
203957
1628981
1627827
1641745
1631323
1628368
1629655
1629636
1630568
1641718
202331
201959
1630581
1628983
1630264
1631221
203497
203932
201569
203

In [29]:
game_log_dict_23 = {k: v for k, v in game_log_dict_24.items() if k in id_list and k in list(player_details['PERSON_ID'])}
game_log_dict_24 = {k: v for k, v in game_log_dict_24.items() if k in id_list and k in list(player_details['PERSON_ID'])}


## This is the start of creating the data tables for prediction

### First Step gettings some modes

In [33]:

for player in game_log_dict_23:

    game_date = pd.to_datetime(game_log_dict_23[player]['GAME_DATE'])

    # Calculate the difference between each date and today's date
    game_log_dict_23[player]['DAYS_SINCE_TODAY'] = (datetime.now() - game_date).dt.days

    game_log_dict_23[player]['GAME_DATE'] = game_date.dt.strftime('%Y/%m/%d')


for player in game_log_dict_24:
    # Get the mode of POSITION, WEIGHT, and HEIGHT_INCHES
    print(player)
    position_mode = player_details.loc[player_details['PERSON_ID'] == player, 'POSITION'].mode()[0]
    weight_mode = player_details.loc[player_details['PERSON_ID'] == player, 'WEIGHT'].mode()[0]
    height_mode = player_details.loc[player_details['PERSON_ID'] == player, 'HEIGHT_INCHES'].mode()[0]
    name_mode = player_details.loc[player_details['PERSON_ID'] == player, 'PLAYER'].mode()[0]

    # Assign these values to the entire column for the player
    game_log_dict_23[player]['POSITION'] = position_mode
    game_log_dict_23[player]['WEIGHT'] = weight_mode
    game_log_dict_23[player]['HEIGHT_INCHES'] = height_mode
    game_log_dict_23[player]['PLAYER_NAME'] = name_mode
    game_log_dict_24[player]['POSITION'] = position_mode
    game_log_dict_24[player]['WEIGHT'] = weight_mode
    game_log_dict_24[player]['HEIGHT_INCHES'] = height_mode
    game_log_dict_24[player]['PLAYER_NAME'] = name_mode
    game_date = pd.to_datetime(game_log_dict_24[player]['GAME_DATE'])

    # Calculate the difference between each date and today's date
    game_log_dict_24[player]['DAYS_SINCE_TODAY'] = (datetime.now() - game_date).dt.days

    game_log_dict_24[player]['GAME_DATE'] = game_date.dt.strftime('%Y/%m/%d')

1630173
1628389
1630534
1630583
1629638
1628960
1628386
1630631
203937
203507
1630175
1628384
1630166
1629028
1628963
1631116
1630163
1628964
1631094
1630217
1630625
1631230
203084
1630567
1629628
1629646
1641734
201587
203078
1627736
1630699
1630180
1629048
1641710
203992
202711
1629626
1626164
1630527
1628449
1631103
1631128
1628969
1628970
1627763
1628415
1628971
1627759
1641738
1628973
1628418
1641723
202692
1630215
202710
1631288
203484
1641739
203991
1628975
1628976
1630618
1627936
1630658
1630577
1630551
1631108
1631321
1629634
203903
1629651
1641730
1629599
1628381
1628380
201144
1626192
1641731
1641741
1628470
1630595
203552
201939
1630700
203076
1631098
1631120
201942
1628978
1631217
1641711
1631172
203915
1629029
1629652
1630245
1630288
203083
1630537
1630561
1627739
201142
1631105
1631106
1630162
1630556
1631165
203954
1629234
203957
1628981
1627827
1641745
1631323
1628368
1629655
1629636
1630568
1641718
202331
201959
1630581
1628983
1630264
1631221
203497
203932
201569
203

### Creating new data tables

In [35]:
game_log_23_by_id = {}
game_log_23_by_player = {}
game_log_24_by_id = {}
game_log_24_by_player = {}

for player_id, df in game_log_dict_23.items():
    print(player_id)
    # Assuming you have a way to get the player's name from the dataframe or a separate source
    player_name = player_details.loc[player_details['PERSON_ID'] == player_id, 'PLAYER'].values[0]  # Get player name

    # Assign the same dataframe to both the player_id and player_name keys
    game_log_23_by_id[player_id] = df[::-1]
    game_log_23_by_player[player_name] = df[::-1]


for player_id, df in game_log_dict_24.items():
    # Assuming you have a way to get the player's name from the dataframe or a separate source
    player_name = player_details.loc[player_details['PERSON_ID'] == player_id, 'PLAYER'].values[0]  # Get player name

    # Assign the same dataframe to both the player_id and player_name keys
    game_log_24_by_id[player_id] = df[::-1]
    game_log_24_by_player[player_name] = df[::-1]

id_list2 = list(game_log_24_by_id.keys())
game_log_23_by_id = {k: v for k, v in game_log_23_by_id.items() if k in id_list2}

1630173
1628389
1630534
1630583
1629638
1628960
1628386
1630631
203937
203507
1630175
1628384
1630166
1629028
1628963
1631116
1630163
1628964
1631094
1630217
1630625
1631230
203084
1630567
1629628
1629646
1641734
201587
203078
1627736
1630699
1630180
1629048
1641710
203992
202711
1629626
1626164
1630527
1628449
1631103
1631128
1628969
1628970
1627763
1628415
1628971
1627759
1641738
1628973
1628418
1641723
202692
1630215
202710
1631288
203484
1641739
203991
1628975
1628976
1630618
1627936
1630658
1630577
1630551
1631108
1631321
1629634
203903
1629651
1641730
1629599
1628381
1628380
201144
1626192
1641731
1641741
1628470
1630595
203552
201939
1630700
203076
1631098
1631120
201942
1628978
1631217
1641711
1631172
203915
1629029
1629652
1630245
1630288
203083
1630537
1630561
1627739
201142
1631105
1631106
1630162
1630556
1631165
203954
1629234
203957
1628981
1627827
1641745
1631323
1628368
1629655
1629636
1630568
1641718
202331
201959
1630581
1628983
1630264
1631221
203497
203932
201569
203

### Creating Progressive Average Stats by each game

In [38]:

# Do the same for game_log_23_by_id
for id in game_log_23_by_id:
    game_log_23_by_id[id]['Progressive_Avg_PTS'] = game_log_23_by_id[id]['PTS'].copy().shift().expanding().mean() 
    game_log_23_by_id[id]['Progressive_Avg_AST'] = game_log_23_by_id[id]['AST'].copy().shift().expanding().mean()
    game_log_23_by_id[id]['Progressive_Avg_REB'] = game_log_23_by_id[id]['REB'].copy().shift().expanding().mean()
    game_log_23_by_id[id]['Progressive_Avg_FGA'] = game_log_23_by_id[id]['FGA'].copy().shift().expanding().mean()
    game_log_23_by_id[id]['Progressive_Avg_FGM'] = game_log_23_by_id[id]['FGM'].copy().shift().expanding().mean()
    game_log_23_by_id[id]['Progressive_Avg_FG_PCT'] = game_log_23_by_id[id]['Progressive_Avg_FGM'].copy() / game_log_23_by_id[id]['Progressive_Avg_FGA'].copy()
    game_log_23_by_id[id]['Progressive_Avg_FG3A'] = game_log_23_by_id[id]['FG3A'].copy().shift().expanding().mean()
    game_log_23_by_id[id]['Progressive_Avg_FG3M'] = game_log_23_by_id[id]['FG3M'].copy().shift().expanding().mean()
    game_log_23_by_id[id]['Progressive_Avg_FG3_PCT'] = game_log_23_by_id[id]['Progressive_Avg_FG3M'].copy() / game_log_23_by_id[id]['Progressive_Avg_FG3A'].copy()
    game_log_23_by_id[id]['Progressive_Avg_FTA'] = game_log_23_by_id[id]['FTA'].copy().shift().expanding().mean()
    game_log_23_by_id[id]['Progressive_Avg_FTM'] = game_log_23_by_id[id]['FTM'].copy().shift().expanding().mean()
    game_log_23_by_id[id]['Progressive_Avg_FT_PCT'] = game_log_23_by_id[id]['Progressive_Avg_FTM'].copy() / game_log_23_by_id[id]['Progressive_Avg_FTA'].copy()
    game_log_23_by_id[id]['Progressive_Avg_STL'] = game_log_23_by_id[id]['STL'].copy().shift().expanding().mean()
    game_log_23_by_id[id]['Progressive_Avg_BLK'] = game_log_23_by_id[id]['BLK'].copy().shift().expanding().mean()
    game_log_23_by_id[id]['Progressive_Avg_TOV'] = game_log_23_by_id[id]['TOV'].copy().shift().expanding().mean()
    game_log_23_by_id[id]['Progressive_Avg_MIN'] = game_log_23_by_id[id]['MIN'].copy().shift().expanding().mean()


# 2024
for id in game_log_24_by_id:
    game_log_24_by_id[id]['Progressive_Avg_PTS'] = game_log_24_by_id[id]['PTS'].copy().shift().expanding().mean() 
    game_log_24_by_id[id]['Progressive_Avg_AST'] = game_log_24_by_id[id]['AST'].copy().shift().expanding().mean()
    game_log_24_by_id[id]['Progressive_Avg_REB'] = game_log_24_by_id[id]['REB'].copy().shift().expanding().mean()
    game_log_24_by_id[id]['Progressive_Avg_FGA'] = game_log_24_by_id[id]['FGA'].copy().shift().expanding().mean()
    game_log_24_by_id[id]['Progressive_Avg_FGM'] = game_log_24_by_id[id]['FGM'].copy().shift().expanding().mean()
    game_log_24_by_id[id]['Progressive_Avg_FG_PCT'] = game_log_24_by_id[id]['Progressive_Avg_FGM'].copy() / game_log_24_by_id[id]['Progressive_Avg_FGA'].copy()
    game_log_24_by_id[id]['Progressive_Avg_FG3A'] = game_log_24_by_id[id]['FG3A'].copy().shift().expanding().mean()
    game_log_24_by_id[id]['Progressive_Avg_FG3M'] = game_log_24_by_id[id]['FG3M'].copy().shift().expanding().mean()
    game_log_24_by_id[id]['Progressive_Avg_FG3_PCT'] = game_log_24_by_id[id]['Progressive_Avg_FG3M'].copy() / game_log_24_by_id[id]['Progressive_Avg_FG3A'].copy()
    game_log_24_by_id[id]['Progressive_Avg_FTA'] = game_log_24_by_id[id]['FTA'].copy().shift().expanding().mean()
    game_log_24_by_id[id]['Progressive_Avg_FTM'] = game_log_24_by_id[id]['FTM'].copy().shift().expanding().mean()
    game_log_24_by_id[id]['Progressive_Avg_FT_PCT'] = game_log_24_by_id[id]['Progressive_Avg_FTM'].copy() / game_log_24_by_id[id]['Progressive_Avg_FTA'].copy()
    game_log_24_by_id[id]['Progressive_Avg_STL'] = game_log_24_by_id[id]['STL'].copy().shift().expanding().mean()
    game_log_24_by_id[id]['Progressive_Avg_BLK'] = game_log_24_by_id[id]['BLK'].copy().shift().expanding().mean()
    game_log_24_by_id[id]['Progressive_Avg_TOV'] = game_log_24_by_id[id]['TOV'].copy().shift().expanding().mean()
    game_log_24_by_id[id]['Progressive_Avg_MIN'] = game_log_24_by_id[id]['MIN'].copy().shift().expanding().mean()


    

C:\Users\jam2m\AppData\Local\Temp\ipykernel_11160\472064976.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  game_log_23_by_id[id]['Progressive_Avg_PTS'] = game_log_23_by_id[id]['PTS'].copy().shift().expanding().mean()
C:\Users\jam2m\AppData\Local\Temp\ipykernel_11160\472064976.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  game_log_23_by_id[id]['Progressive_Avg_AST'] = game_log_23_by_id[id]['AST'].copy().shift().expanding().mean()
C:\Users\jam2m\AppData\Local\Temp\ipykernel_11160\472064976.py:5: Se

### Similar to last, but this time creating 10 game averages

In [42]:
# Function to calculate 10-game averages excluding the current day's game
def calculate_10_game_avg_excluding_current(df, column):
    return df[column].shift().rolling(window=10, min_periods=1).mean()

# Process 2023 data
for id in game_log_23_by_id:
    df = game_log_23_by_id[id].copy()
    
    for stat in ['PTS', 'AST', 'REB', 'FGA', 'FGM', 'FG3A', 'FG3M', 'FTA', 'FTM', 'STL', 'BLK', 'TOV', 'MIN']:
        df[f'10_Game_Avg_{stat}'] = calculate_10_game_avg_excluding_current(df, stat)
    
    # Calculate percentages
    df['10_Game_Avg_FG_PCT'] = df['10_Game_Avg_FGM'] / df['10_Game_Avg_FGA']
    df['10_Game_Avg_FG3_PCT'] = df['10_Game_Avg_FG3M'] / df['10_Game_Avg_FG3A']
    df['10_Game_Avg_FT_PCT'] = df['10_Game_Avg_FTM'] / df['10_Game_Avg_FTA']
    
    # Set first entry to 0
    for col in df.columns:
        if col.startswith('10_Game_Avg_'):
            df.loc[df.index[0], col] = 0
    
    game_log_23_by_id[id] = df.copy()

# Process 2024 data
for id in game_log_24_by_id:
    df_24 = game_log_24_by_id[id].copy()
    
    if id in game_log_23_by_id:
        df_23 = game_log_23_by_id[id].copy()
        # Combine last 9 games of 2023 with 2024 data
        df_combined = pd.concat([df_23.tail(9), df_24])
    else:
        df_combined = df_24.copy()
    
    for stat in ['PTS', 'AST', 'REB', 'FGA', 'FGM', 'FG3A', 'FG3M', 'FTA', 'FTM', 'STL', 'BLK', 'TOV', 'MIN']:
        df_24[f'10_Game_Avg_{stat}'] = calculate_10_game_avg_excluding_current(df_combined, stat).tail(len(df_24))
    
    # Calculate percentages
    df_24['10_Game_Avg_FG_PCT'] = df_24['10_Game_Avg_FGM'] / df_24['10_Game_Avg_FGA']
    df_24['10_Game_Avg_FG3_PCT'] = df_24['10_Game_Avg_FG3M'] / df_24['10_Game_Avg_FG3A']
    df_24['10_Game_Avg_FT_PCT'] = df_24['10_Game_Avg_FTM'] / df_24['10_Game_Avg_FTA']
    
    game_log_24_by_id[id] = df_24.copy()

# Handle division by zero and NaN values
for id in game_log_23_by_id:
    game_log_23_by_id[id] = game_log_23_by_id[id].replace([np.inf, -np.inf], np.nan).fillna(0)

for id in game_log_24_by_id:
    game_log_24_by_id[id] = game_log_24_by_id[id].replace([np.inf, -np.inf], np.nan).fillna(0)

### Sorting to keep players who played over 20 mpg

In [44]:
def calculate_avg_minutes(player_df):
    return player_df['MIN'].mean()

# Step 1 & 2: Calculate average minutes and filter players
players_2023 = {}
players_2024 = {}

for player_id, df in game_log_23_by_id.items():
    avg_minutes = calculate_avg_minutes(df)
    
    if avg_minutes >= 20 and df.shape[0] > 40:
        players_2023[player_id] = avg_minutes

for player_id, df in game_log_24_by_id.items():
    avg_minutes = calculate_avg_minutes(df)
    
    if avg_minutes >= 20 and df.shape[0] > 3:
        players_2024[player_id] = avg_minutes

# Step 3: Keep only players present in both seasons
common_players = set(players_2023.keys()) & set(players_2024.keys())

# Filter the original dictionaries
game_log_23_by_id = {player_id: df for player_id, df in game_log_23_by_id.items() if player_id in common_players}
game_log_24_by_id = {player_id: df for player_id, df in game_log_24_by_id.items() if player_id in common_players}

In [50]:
players_2023

{1630173: 21.945945945945947,
 1628389: 34.014084507042256,
 1630534: 21.012820512820515,
 1630583: 26.57377049180328,
 1629638: 23.475609756097562,
 1628960: 33.50666666666667,
 1628386: 31.7012987012987,
 203937: 22.518987341772153,
 203507: 35.24657534246575,
 1630175: 22.444444444444443,
 1628384: 34.1,
 1630166: 30.12,
 1629028: 32.41818181818182,
 1628963: 21.02,
 1631094: 34.975,
 1630217: 34.357142857142854,
 203084: 29.01219512195122,
 1630567: 34.93333333333333,
 1629628: 31.689655172413794,
 201587: 25.466666666666665,
 203078: 33.37735849056604,
 1627736: 29.59493670886076,
 1630180: 32.698412698412696,
 203992: 30.40506329113924,
 202711: 25.964912280701753,
 1626164: 35.955882352941174,
 1631103: 21.213333333333335,
 1631128: 20.195121951219512,
 1628969: 34.81707317073171,
 1628970: 37.47826086956522,
 1628415: 30.930555555555557,
 1628971: 27.850746268656717,
 1627759: 33.457142857142856,
 1628973: 35.44155844155844,
 202710: 34.03333333333333,
 203484: 31.6315789473684

### this next code creates expected increase or decrease in points based on team played and player position

In [53]:
game_log_23_by_id[203999]['DAYS_SINCE_TODAY']

78    397
77    394
76    392
75    391
74    389
     ... 
4     232
3     229
2     228
1     226
0     224
Name: DAYS_SINCE_TODAY, Length: 79, dtype: int64

In [71]:
team_list = list(game_log_23_by_id[203999]['OPP'].unique())
team_list.append('DEN')
position = ['G', 'F', 'C']

team_position_dict_23 = {}
team_position_dict_24 = {}



# Create empty lists for each team and position combination
for team in team_list:
    for pos in position:
        team_position_dict_23[f"{team}_{pos}"] = []
        team_position_dict_24[f"{team}_{pos}"] = []

# Getting average amount above avg based on team played for each position
for id in game_log_23_by_id:
    df = game_log_23_by_id[id].copy()
    position = df['POSITION'][0]
    for index, row in df.iterrows():
        if row['MIN'] > 19:
            team = row['OPP']  # The team the player played against
            points = row['PTS']
    
            key = f"{team}_{position}"
    
            if key in team_position_dict_23:
                team_position_dict_23[key].append(points)

for id in game_log_24_by_id:
    df = game_log_24_by_id[id].copy()
    position = df['POSITION'][0]
    for index, row in df.iterrows():
        if row['MIN'] > 19:
            team = row['OPP']  # The team the player played against
            points = row['PTS']
    
            key = f"{team}_{position}"
    
            if key in team_position_dict_24:
                team_position_dict_24[key].append(points)
    


points_averages_23 = {}
guard_averages_23 = []
forward_averages_23 = []
center_averages_23 = []

points_averages_24 = {}
guard_averages_24 = []
forward_averages_24 = []
center_averages_24 = []

for id in team_position_dict_23:
    if id[4] == 'G':
        guard_averages_23.append(pd.to_numeric(team_position_dict_23[id]).mean())
    elif id[4] == 'F':
        forward_averages_23.append(pd.to_numeric(team_position_dict_23[id]).mean())
    elif id[4] == 'C':
        center_averages_23.append(pd.to_numeric(team_position_dict_23[id]).mean())
        
guard_mean_23 = pd.to_numeric(guard_averages_23).mean()
forward_mean_23 = pd.to_numeric(forward_averages_23).mean()
center_mean_23 = pd.to_numeric(center_averages_23).mean()
for id in team_position_dict_23:
    if id[4] == 'G':  
        points_averages_23[id] = pd.to_numeric(team_position_dict_23[id]).mean() - guard_mean_23
    if id[4] == 'F':  
        points_averages_23[id] = pd.to_numeric(team_position_dict_23[id]).mean() - forward_mean_23
    if id[4] == 'C':  
        points_averages_23[id] = pd.to_numeric(team_position_dict_23[id]).mean() - center_mean_23



for id in team_position_dict_24:
    if id[4] == 'G':
        guard_averages_24.append(pd.to_numeric(team_position_dict_24[id]).mean())
    elif id[4] == 'F':
        forward_averages_24.append(pd.to_numeric(team_position_dict_24[id]).mean())
    elif id[4] == 'C':
        center_averages_24.append(pd.to_numeric(team_position_dict_24[id]).mean())
        
guard_mean_24 = pd.to_numeric(guard_averages_24).mean()
forward_mean_24 = pd.to_numeric(forward_averages_24).mean()
center_mean_24 = pd.to_numeric(center_averages_24).mean()
for id in team_position_dict_24:
    if id[4] == 'G':  
        points_averages_24[id] = pd.to_numeric(team_position_dict_24[id]).mean() - guard_mean_24
    if id[4] == 'F':  
        points_averages_24[id] = pd.to_numeric(team_position_dict_24[id]).mean() - forward_mean_24
    if id[4] == 'C':  
        points_averages_24[id] = pd.to_numeric(team_position_dict_24[id]).mean() - center_mean_24
        

def add_position_averages_to_gamelog(game_log_df, player_position, points_averages):
    # Create a new column to store the average value from the dictionary
    game_log_df['AVG_ABOVE_NORM_BY_POS_TEAM'] = None
    
    # Iterate over the rows in the game log
    for index, row in game_log_df.iterrows():
        team = row['OPP']  # Assuming 'OPP' contains the opposing team (e.g., 'BOS', 'LAL')
        position = player_position  # The player's position (e.g., 'G', 'F', 'C')

        # Create the key in {team_pos} format
        key = f'{team}_{position}'

        # Look up the corresponding value in the dictionary and add it to the DataFrame
        if key in team_position_dict_23:
            game_log_df.at[index, 'AVG_ABOVE_NORM_BY_POS_TEAM'] = points_averages[key]
        else:
            game_log_df.at[index, 'AVG_ABOVE_NORM_BY_POS_TEAM'] = None  # If no match, you can set this to None or 0

for id in game_log_23_by_id:
    position = game_log_23_by_id[id]['POSITION'][0]
    add_position_averages_to_gamelog(game_log_23_by_id[id], position, points_averages_23) 

for id in game_log_24_by_id:
    position = game_log_24_by_id[id]['POSITION'][0]
    add_position_averages_to_gamelog(game_log_24_by_id[id], position, points_averages_24) 

            

### This is code we will not use for now. The goal was to create dynamic averages across positions and teams but IDK if I've done it right. Instead we will use the previous code but not use for these predictions, only use it for the player prop predictions. 

from collections import defaultdict

##### Combine all games into a single DataFrame
all_games = []

for id in game_log_23_by_id:
    df = game_log_23_by_id[id].copy()
    df['Player_ID'] = id
    all_games.append(df)

for id in game_log_24_by_id:
    df = game_log_24_by_id[id].copy()
    df['Player_ID'] = id
    all_games.append(df)

combined_df = pd.concat(all_games).sort_values(by='DAYS_SINCE_TODAY')  # Ensure 'Date' is a column in your DataFrames

##### Initialize dictionaries to store cumulative points and counts
cumulative_points = defaultdict(lambda: defaultdict(int))
cumulative_counts = defaultdict(lambda: defaultdict(int))

##### Calculate dynamic averages
dynamic_averages = []

for index, row in combined_df.iterrows():
    team = row['OPP']
    position = row['POSITION']
    key = f"{team}_{position}"

    # Calculate average if there are previous games
    if cumulative_counts[team][position] > 0:
        avg = cumulative_points[team][position] / cumulative_counts[team][position]
    else:
        avg = 0  # Default value if no previous games

    dynamic_averages.append(avg)

    # Update cumulative points and counts
    cumulative_points[team][position] += row['PTS']
    cumulative_counts[team][position] += 1

##### Ensure unique indices in combined_df
combined_df = combined_df.reset_index(drop=True)
'''
##### Update individual game logs with the calculated averages
for id in game_log_23_by_id:
    # Ensure the indices match by resetting and aligning
    game_log_23_by_id[id] = game_log_23_by_id[id].reset_index(drop=True)
    dynamic_avg_series = combined_df[combined_df['Player_ID'] == id]['Dynamic_Avg_PTS'].reset_index(drop=True)
    
    # Assign the dynamic averages
    game_log_23_by_id[id]['Dynamic_Avg_PTS'] = dynamic_avg_series

for id in game_log_24_by_id:
    # Ensure the indices match by resetting and aligning
    game_log_24_by_id[id] = game_log_24_by_id[id].reset_index(drop=True)
    dynamic_avg_series = combined_df[combined_df['Player_ID'] == id]['Dynamic_Avg_PTS'].reset_index(drop=True)
    
    # Assign the dynamic averages
    game_log_24_by_id[id]['Dynamic_Avg_PTS'] = dynamic_avg_series
'''

### This calculated Progressive Averages again I guess I messed up in the first code?

In [74]:
# Now, let's process the 2023 data
for player_id in game_log_23_by_id:
    df = game_log_23_by_id[player_id].copy()
    
    # Calculate non-percentage stats
    for stat in ['PTS', 'AST', 'REB', 'FGA', 'FG3A', 'FTA', 'STL', 'BLK', 'TOV', 'MIN']:
        df[f'Progressive_Avg_{stat}'] = df[stat].copy().expanding().mean()
    
    # Calculate percentage stats correctly
    df['Progressive_Avg_FG_PCT'] = df['FGM'].copy().expanding().sum() / df['FGA'].copy().expanding().sum()
    print(df['Progressive_Avg_FG_PCT'], df['FGM'], df['FGA'])
    df['Progressive_Avg_FG3_PCT'] = df['FG3M'].copy().expanding().sum() / df['FG3A'].copy().expanding().sum()
    df['Progressive_Avg_FT_PCT'] = df['FTM'].copy().expanding().sum() / df['FTA'].copy().expanding().sum()
    
    # Replace NaN and inf values with 0
    df = df.replace([np.inf, -np.inf], np.nan).fillna(0)
    
    # Update the dictionary with the modified DataFrame
    game_log_23_by_id[player_id] = df.copy()



# Now, let's process the 2024 data
for player_id in game_log_24_by_id:
    df = game_log_24_by_id[player_id].copy()
    first_index = df.index[0]
    
    # Calculate non-percentage stats
    for stat in ['PTS', 'AST', 'REB', 'FGA', 'FG3A', 'FTA', 'STL', 'BLK', 'TOV', 'MIN']:
        df[f'Progressive_Avg_{stat}'] = df[stat].copy().expanding().mean()
        # Fill the first row with the player's average from 2022 if available
        if player_id in game_log_23_by_id:
            df.loc[first_index, f'Progressive_Avg_{stat}'] = game_log_23_by_id[player_id][stat].mean()
    
    # Calculate percentage stats correctly
    df['Progressive_Avg_FG_PCT'] = df['FGM'].copy().expanding().sum() / df['FGA'].copy().expanding().sum()
    df['Progressive_Avg_FG3_PCT'] = df['FG3M'].copy().expanding().sum() / df['FG3A'].copy().expanding().sum()
    df['Progressive_Avg_FT_PCT'] = df['FTM'].copy().expanding().sum() / df['FTA'].copy().expanding().sum()
    
    # Fill the first row of percentage stats with the player's average from 2022 if available
    if player_id in game_log_23_by_id:
        df.loc[first_index, 'Progressive_Avg_FG_PCT'] = game_log_23_by_id[player_id]['FGM'].copy().sum() / game_log_23_by_id[player_id]['FGA'].copy().sum()
        df.loc[first_index, 'Progressive_Avg_FG3_PCT'] = game_log_23_by_id[player_id]['FG3M'].copy().sum() / game_log_23_by_id[player_id]['FG3A'].copy().sum()
        df.loc[first_index, 'Progressive_Avg_FT_PCT'] = game_log_23_by_id[player_id]['FTM'].copy().sum() / game_log_23_by_id[player_id]['FTA'].copy().sum()
    
    # Replace NaN and inf values with 0
    df = df.replace([np.inf, -np.inf], np.nan).fillna(0)
    
    # Update the dictionary with the modified DataFrame
    game_log_24_by_id[player_id] = df.copy()


73    0.444444
72    0.428571
71    0.375000
70    0.344828
69    0.405405
        ...   
4     0.503282
3     0.502183
2     0.497845
1     0.500000
0     0.501066
Name: Progressive_Avg_FG_PCT, Length: 74, dtype: float64 73    4
72    2
71    3
70    1
69    5
     ..
4     0
3     0
2     1
1     2
0     2
Name: FGM, Length: 74, dtype: int64 73     9
72     5
71    10
70     5
69     8
      ..
4      2
3      1
2      6
1      2
0      3
Name: FGA, Length: 74, dtype: int64
70    0.538462
69    0.472222
68    0.480000
67    0.516129
66    0.519481
        ...   
4     0.519467
3     0.519309
2     0.515547
1     0.518371
0     0.521141
Name: Progressive_Avg_FG_PCT, Length: 71, dtype: float64 70     7
69    10
68     7
67     8
66     8
      ..
4      8
3      4
2      3
1      8
0      8
Name: FGM, Length: 71, dtype: int64 70    13
69    23
68    14
67    12
66    15
      ..
4     18
3      8
2     13
1     10
0     10
Name: FGA, Length: 71, dtype: int64
77    0.333333
76    0.3333

C:\Users\jam2m\AppData\Local\Temp\ipykernel_11160\1007391052.py:16: FutureWarning: Downcasting behavior in `replace` is deprecated and will be removed in a future version. To retain the old behavior, explicitly call `result.infer_objects(copy=False)`. To opt-in to the future behavior, set `pd.set_option('future.no_silent_downcasting', True)`
  df = df.replace([np.inf, -np.inf], np.nan).fillna(0)


49    1.000000
48    0.666667
47    0.650000
46    0.666667
45    0.558824
44    0.536585
43    0.543478
42    0.537037
41    0.566667
40    0.578125
39    0.565789
38    0.590909
37    0.591398
36    0.597938
35    0.590909
34    0.586207
33    0.583333
32    0.579365
31    0.574803
30    0.574627
29    0.572414
28    0.573248
27    0.591716
26    0.589595
25    0.588571
24    0.591160
23    0.593909
22    0.578704
21    0.577778
20    0.587983
19    0.592437
18    0.587755
17    0.593625
16    0.596899
15    0.584906
14    0.585455
13    0.577855
12    0.575758
11    0.572816
10    0.567398
9     0.572727
8     0.581395
7     0.580737
6     0.575000
5     0.574932
4     0.581333
3     0.584416
2     0.588832
1     0.588089
0     0.585784
Name: Progressive_Avg_FG_PCT, dtype: float64 49     3
48     5
47     5
46     3
45     3
44     3
43     3
42     4
41     5
40     3
39     6
38     9
37     3
36     3
35     7
34     3
33     2
32     3
31     0
30     4
29     6
28     7
27    1

C:\Users\jam2m\AppData\Local\Temp\ipykernel_11160\1007391052.py:47: FutureWarning: Downcasting behavior in `replace` is deprecated and will be removed in a future version. To retain the old behavior, explicitly call `result.infer_objects(copy=False)`. To opt-in to the future behavior, set `pd.set_option('future.no_silent_downcasting', True)`
  df = df.replace([np.inf, -np.inf], np.nan).fillna(0)
C:\Users\jam2m\AppData\Local\Temp\ipykernel_11160\1007391052.py:47: FutureWarning: Downcasting behavior in `replace` is deprecated and will be removed in a future version. To retain the old behavior, explicitly call `result.infer_objects(copy=False)`. To opt-in to the future behavior, set `pd.set_option('future.no_silent_downcasting', True)`
  df = df.replace([np.inf, -np.inf], np.nan).fillna(0)
C:\Users\jam2m\AppData\Local\Temp\ipykernel_11160\1007391052.py:47: FutureWarning: Downcasting behavior in `replace` is deprecated and will be removed in a future version. To retain the old behavior, ex

### Makes sure that the ids match in both once again

In [76]:
id_list2 = list(game_log_24_by_id.keys())
game_log_23_by_id = {k: v for k, v in game_log_23_by_id.items() if k in id_list2}


# Make all names lower case to make matching with player prop data easier

In [78]:
for id in game_log_24_by_id:
    game_log_24_by_id[id]['PLAYER_NAME'] = game_log_24_by_id[id]['PLAYER_NAME'].apply(lambda x: x.lower())
    game_log_23_by_id[id]['PLAYER_NAME'] = game_log_23_by_id[id]['PLAYER_NAME'].apply(lambda x: x.lower())


In [79]:
print(game_log_24_by_id.keys())

dict_keys([1630173, 1628389, 1630534, 1630583, 1629638, 1628960, 1628386, 203937, 203507, 1630175, 1628384, 1630166, 1629028, 1628963, 1631094, 1630217, 203084, 1630567, 1629628, 201587, 203078, 1627736, 1630180, 203992, 202711, 1626164, 1631103, 1631128, 1628969, 1628970, 1628415, 1628971, 1627759, 1628973, 202710, 203484, 1641739, 203991, 1628976, 1627936, 203903, 1629651, 1629599, 1628381, 1628380, 201144, 1626192, 1641731, 1630595, 201939, 1630700, 203076, 201942, 1628978, 1641711, 203915, 1629029, 1629652, 1630245, 201142, 1631105, 1630162, 1627827, 1631323, 1628368, 1629655, 1629636, 1641718, 202331, 1630581, 1628983, 203497, 203932, 201569, 203924, 203110, 1630224, 1630182, 1629656, 1629060, 1630169, 203501, 201935, 203914, 202699, 1628404, 1628392, 1630573, 1630703, 1629639, 1627741, 1629312, 201950, 1631096, 201143, 1628989, 1629631, 1627742, 202681, 1631093, 202704, 1641713, 1628991, 2544, 1631170, 1629661, 1630552, 1629640, 203999, 1630529, 1630200, 1626145, 1627884, 1631117

### Saving these dictionaries to my repository so they do not have to run again

### Retrieves dictionaries

In [234]:
game_log_23_by_id[1628973]['WEIGHT']

76    190.0
75    190.0
74    190.0
73    190.0
72    190.0
      ...  
4     190.0
3     190.0
2     190.0
1     190.0
0     190.0
Name: WEIGHT, Length: 77, dtype: float64

In [166]:
player_props = pd.read_csv('prop_table.csv', index_col= 0)

# Test modeling:
#### This code just makes predictions on prior data with 2 main goals:
1. Be as accurate as possible to prior data. These predicitions will be used as place holders for player props for data I could not get
2. Test if my predictions are good as I will be using a lot of the same predictors for the classification model of predicting over under data. 

In [220]:
point_predictions = []
real_points = []
training_set = pd.concat([game_log_24_by_id[1628973].iloc[:20, :], game_log_23_by_id[1628973]])

today = datetime.now().date()
for id in list(game_log_24_by_id.keys()):
    
    length = len(game_log_24_by_id[id])
    for i in range(20, length):
    
        player_name = game_log_24_by_id[id]['PLAYER_NAME'][0]
        features = ['Progressive_Avg_PTS', 'Progressive_Avg_AST', 'Progressive_Avg_REB',
            'Progressive_Avg_FG_PCT', 'Progressive_Avg_FGA', 'Progressive_Avg_FG3A',
            'Progressive_Avg_FG3_PCT', 'Progressive_Avg_FTA',
            'Progressive_Avg_FT_PCT', 'Progressive_Avg_STL', 'Progressive_Avg_BLK',
            'Progressive_Avg_TOV', 'Progressive_Avg_MIN','10_Game_Avg_PTS',
            '10_Game_Avg_AST', '10_Game_Avg_REB', '10_Game_Avg_FGA',
            '10_Game_Avg_FG3A', '10_Game_Avg_FTA', '10_Game_Avg_STL',
            '10_Game_Avg_BLK', '10_Game_Avg_TOV', '10_Game_Avg_MIN',
            '10_Game_Avg_FG_PCT', '10_Game_Avg_FG3_PCT', '10_Game_Avg_FT_PCT', 'WEIGHT',
            'HEIGHT_INCHES', 'DAYS_SINCE_TODAY']
    
        # Create a pipeline for feature processing
        feature_pipeline = Pipeline([
            ('scaler', StandardScaler())
        ])
        
        # Prepare training data
        X_train = training_set.loc[:, features]
        y_train = training_set['PTS']
        
        # Fit and transform the training data
        X_train_processed = feature_pipeline.fit_transform(X_train)
        
        # Prepare test data
        test_set = game_log_24_by_id[id].iloc[i, :]
        X_test = test_set.loc[features].to_frame().T
        
        # Transform the test data
        X_test_processed = feature_pipeline.transform(X_test)
        y_test = test_set['PTS']
        y_test_array = np.array([y_test])
    
    
        tscv = TimeSeriesSplit(n_splits=5)  # You can adjust the number of splits
    
        alphas = np.logspace(0,-4,200)
        lassocv = LassoCV(
        cv=tscv,  # Use the TimeSeriesSplit we defined earlier
        max_iter=10000,  # Reduce max iterations
        tol=1e-4,  # Set a tolerance for early stopping
        n_jobs=-1
    )
        lassocv.fit(X_train, y_train)
        
        lasso_prediction = lassocv.predict(X_test)


        random_forest = RandomForestRegressor(n_estimators=100, random_state=42, max_features=.5, bootstrap=False)

        # Fit the Random Forest model
        random_forest.fit(X_train_processed, y_train)
        
        # Make predictions with the Random Forest model
        rf_prediction = random_forest.predict(X_test_processed)

        prediction = (lasso_prediction + rf_prediction)/2

        
        training_set = pd.concat([game_log_24_by_id[id].iloc[:i+1, :], game_log_23_by_id[id]])
    
        
        date = (today - timedelta(days = int(test_set['DAYS_SINCE_TODAY']))).strftime('%Y/%m/%d')
        player_props.loc[player_props['date'] == date, f'{player_name}_line'] = prediction
        player_props.loc[player_props['date'] == date, f'{player_name}_real_score'] = y_test
        if y_test > prediction:
            player_props.loc[player_props['date'] == date, f'{player_name}_ou'] = 'over'
        elif y_test < prediction:
            player_props.loc[player_props['date'] == date, f'{player_name}_ou'] = 'under'
        else:
            player_props.loc[player_props['date'] == date, f'{player_name}_ou'] = 'over/under'
        
        print(i)


20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57


C:\Users\jam2m\anaconda3\Lib\site-packages\sklearn\linear_model\_coordinate_descent.py:697: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations, check the scale of the features or consider increasing regularisation. Duality gap: 1.244e+00, tolerance: 9.340e-02
  model = cd_fast.enet_coordinate_descent(
C:\Users\jam2m\anaconda3\Lib\site-packages\sklearn\linear_model\_coordinate_descent.py:697: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations, check the scale of the features or consider increasing regularisation. Duality gap: 6.444e-01, tolerance: 9.340e-02
  model = cd_fast.enet_coordinate_descent(


58


C:\Users\jam2m\anaconda3\Lib\site-packages\sklearn\linear_model\_coordinate_descent.py:697: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations, check the scale of the features or consider increasing regularisation. Duality gap: 8.160e-02, tolerance: 7.678e-02
  model = cd_fast.enet_coordinate_descent(


59
60
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
20
21
22
23
24


...

20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69


C:\Users\jam2m\AppData\Local\Temp\ipykernel_24696\3859780051.py:75: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  player_props.loc[player_props['date'] == date, f'{player_name}_real_score'] = y_test
C:\Users\jam2m\AppData\Local\Temp\ipykernel_24696\3859780051.py:77: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  player_props.loc[player_props['date'] == date, f'{player_name}_ou'] = 'over'


20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53


C:\Users\jam2m\AppData\Local\Temp\ipykernel_24696\3859780051.py:75: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  player_props.loc[player_props['date'] == date, f'{player_name}_real_score'] = y_test
C:\Users\jam2m\AppData\Local\Temp\ipykernel_24696\3859780051.py:79: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  player_props.loc[player_props['date'] == date, f'{player_name}_ou'] = 'under'


20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67


In [106]:
list(game_log_24_by_id.keys())[-1:]

[1627826]

In [108]:
game_log_24_by_id[1627826]['PLAYER_NAME']

67    ivica zubac
66    ivica zubac
65    ivica zubac
64    ivica zubac
63    ivica zubac
         ...     
4     ivica zubac
3     ivica zubac
2     ivica zubac
1     ivica zubac
0     ivica zubac
Name: PLAYER_NAME, Length: 68, dtype: object

In [224]:
player_props.loc[100:150][['date', 'ivica zubac_line', 'ivica zubac_real_score', 'ivica zubac_ou']]

date  ivica zubac_line  ivica zubac_real_score ivica zubac_ou
100  2024/01/16               NaN                     NaN            NaN
101  2024/01/17               NaN                     NaN            NaN
102  2024/01/18               NaN                     NaN            NaN
103  2024/01/19               NaN                     NaN            NaN
104  2024/01/20               NaN                     NaN            NaN
105  2024/01/21               NaN                     NaN            NaN
106  2024/01/22               NaN                     NaN            NaN
107  2024/01/23               NaN                     NaN            NaN
108  2024/01/24               NaN                     NaN            NaN
109  2024/01/25               NaN                     NaN            NaN
110  2024/01/26               NaN                     NaN            NaN
111  2024/01/27               NaN                     NaN            NaN
112  2024/01/28               NaN                     NaN            NaN
113  2024/01/29               NaN                     NaN            NaN
114  2024/01/30               NaN                     NaN            NaN
115  2024/01/31               NaN                     NaN            NaN
116  2024/02/01               NaN                     NaN            NaN
117  2024/02/02               NaN                     NaN            NaN
118  2024/02/03               NaN                     NaN            NaN
119  2024/02/04               NaN                     NaN            NaN
120  2024/02/05               NaN                     NaN            NaN
121  2024/02/06          7.962264                     4.0          under
122  2024/02/07               NaN                     NaN            NaN
123  2024/02/08               NaN                     NaN            NaN
124  2024/02/09         11.925234                    12.0           over
125  2024/02/10               NaN                     NaN            NaN
126  2024/02/11               NaN                     NaN            NaN
127  2024/02/12          8.925926                     6.0          under
128  2024/02/13               NaN                     NaN            NaN
129  2024/02/14          8.892127                     6.0          under
130  2024/02/15               NaN                     NaN            NaN
131  2024/02/16         12.372727                    13.0           over
132  2024/02/17               NaN                     NaN            NaN
133  2024/02/18               NaN                     NaN            NaN
134  2024/02/19               NaN                     NaN            NaN
135  2024/02/20               NaN                     NaN            NaN
136  2024/02/21               NaN                     NaN            NaN
137  2024/02/22               NaN                     NaN            NaN
138  2024/02/23               NaN                     NaN            NaN
139  2024/02/24         12.378378                    13.0           over
140  2024/02/25         10.883929                    10.0          under
141  2024/02/26               NaN                     NaN            NaN
142  2024/02/27         13.876106                    16.0           over
143  2024/02/28               NaN                     NaN            NaN
144  2024/02/29               NaN                     NaN            NaN
145  2024/03/01               NaN                     NaN            NaN
146  2024/03/02               NaN                     NaN            NaN
147  2024/03/03               NaN                     NaN            NaN
148  2024/03/04               NaN                     NaN            NaN
149  2024/03/05          6.894737                     2.0          under
150  2024/03/06          8.852174                     6.0          under

In [230]:
player_props.to_csv('prop_table.csv')

In [274]:
predictions = []
for d in point_predictions:
    predictions.append(d[0])

In [276]:
for i in range(len(predictions)):
    print(predictions[i] - real_points[i])

2.9649888610438992
4.889802293835199
2.7507353934729224
-24.495348397654727
5.210733665305838
-2.5940388840039255
10.59981545066525
-9.245611431569586
-12.813720173176911
3.8268050981207296
6.8887146605394065
-1.7208400177844538
11.032241780893344
-2.2768075207891343
-2.2234117038770265
-6.3762357009082
16.48239217424063
-3.9251857584582552
-4.178970041515029
-13.976085936333448
-9.166178345236943
-1.471200224833673
7.934007573620114
-3.2679645986255323
-2.8706436162608533
0.7336466593133508
-9.843954374251933
-5.099067282310532
4.211232731820765
-7.669495975045962
5.203852792225582
-1.83583355912468
10.079182731745743
-2.6603352708366117
-3.313490023048196
4.319998805999031
29.62490512705772
1.6548263690912144
9.470644491402766
5.8719048436822625
-18.122103577501527
-14.266272778240161
-4.96728074160054
3.0319435320826074
10.87802978777487
-0.6611135159163126
2.6104904792713945
-30.547776331483508
1.4584235759173971
9.925164690537091
-4.78704802246634
-3.2407788600148564
-10.521032352

In [278]:
real_points

[23,
 21,
 23,
 50,
 22,
 29,
 16,
 36,
 38,
 24,
 20,
 28,
 16,
 31,
 29,
 33,
 12,
 30,
 30,
 41,
 38,
 30,
 21,
 32,
 32,
 29,
 40,
 36,
 27,
 39,
 27,
 33,
 21,
 34,
 35,
 27,
 0,
 26,
 19,
 20,
 45,
 42,
 34,
 26,
 17,
 28,
 26,
 61,
 30,
 20,
 35,
 35,
 43,
 45,
 39,
 30,
 40]

In [280]:
predictions

[25.9649888610439,
 25.8898022938352,
 25.750735393472922,
 25.504651602345273,
 27.21073366530584,
 26.405961115996075,
 26.59981545066525,
 26.754388568430414,
 25.18627982682309,
 27.82680509812073,
 26.888714660539407,
 26.279159982215546,
 27.032241780893344,
 28.723192479210866,
 26.776588296122974,
 26.6237642990918,
 28.48239217424063,
 26.074814241541745,
 25.82102995848497,
 27.023914063666552,
 28.833821654763057,
 28.528799775166327,
 28.934007573620114,
 28.732035401374468,
 29.129356383739147,
 29.73364665931335,
 30.156045625748067,
 30.900932717689468,
 31.211232731820765,
 31.33050402495404,
 32.20385279222558,
 31.16416644087532,
 31.079182731745743,
 31.33966472916339,
 31.686509976951804,
 31.31999880599903,
 29.62490512705772,
 27.654826369091214,
 28.470644491402766,
 25.871904843682263,
 26.877896422498473,
 27.73372722175984,
 29.03271925839946,
 29.031943532082607,
 27.87802978777487,
 27.338886484083687,
 28.610490479271395,
 30.452223668516492,
 31.4584235759